# **SETUP**

In [6]:
! mkdir /root/.kaggle

In [7]:
import json
kaggle_api = {"username":"sz2716", "key":"832255fef541b594540ea172b8cc7604"}
with open(("/root/.kaggle/kaggle.json"), "w") as outfile:
    json.dump(kaggle_api, outfile)

In [8]:
! chmod 600 /root/.kaggle/kaggle.json
! pip install kaggle
! kaggle competitions download -c jigsaw-toxic-comment-classification-challenge
! for f in *.zip; do unzip $f -d /content/data/; done
! unzip /content/data/test.csv.zip -d /content/data/
! unzip /content/data/test_labels.csv.zip -d /content/data/
! unzip /content/data/train.csv.zip -d /content/data/

 85% 45.0M/52.6M [00:00<00:00, 162MB/s] 
100% 52.6M/52.6M [00:00<00:00, 142MB/s]
Archive:  jigsaw-toxic-comment-classification-challenge.zip
  inflating: /content/data/sample_submission.csv.zip  
  inflating: /content/data/test.csv.zip  
  inflating: /content/data/test_labels.csv.zip  
  inflating: /content/data/train.csv.zip  
Archive:  /content/data/test.csv.zip
  inflating: /content/data/test.csv  
Archive:  /content/data/test_labels.csv.zip
  inflating: /content/data/test_labels.csv  
Archive:  /content/data/train.csv.zip
  inflating: /content/data/train.csv  


In [21]:
import pandas as pd
train = pd.read_csv("/content/data/train.csv")
test_x = pd.read_csv("/content/data/test.csv")
test_y = pd.read_csv("/content/data/test_labels.csv")

train['is_toxic'] = train[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']].any(axis='columns')

In [18]:
train.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate  is_toxic  
0             0        0       0       0              0     False  
1             0        0       0       0              0     False  
2             0        0       0       0              0     False  
3             0        0       0       0              0     False  
4             0        0       0       0              0     False

In [12]:
#Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import plotly
import plotly.express as px
import numpy as np
import pandas as pd
import itertools
import re
import string
import nltk
import plotly
import plotly.express as px
import spacy

from collections import Counter
from wordcloud import WordCloud
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from nltk import ne_chunk
from nltk.util import ngrams
from textblob import TextBlob
from IPython.core.display import display, HTML 

#Feature Extraction
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, TfidfTransformer
from nltk.util import ngrams

#Preprocessing
from scipy.sparse import hstack
from sklearn import preprocessing

#Model Evaluation
from sklearn.model_selection import train_test_split, KFold, cross_val_score
from sklearn.metrics import classification_report, fl_score, precision_score, recall_score, precision_recall_curve, fbeta_score
from sklearn.metrics import roc_auc_score, roc_curve

#ML models
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import LinearSVC


nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')

stops = set(stopwords.words('english'))
lmtzr = WordNetLemmatizer()
nlp_ner_model = spacy.load("en_core_web_sm")

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


# **Text Cleaning**

In [ ]:
def lower_case_normalization(text):
  return text.lower()

def clean_punct(text):
  return " ".join([word for word in text.split() if word.isalpha()])

def remove_stop_words(stopwords, text):
  return " ".join([word for word in text.split() if word not in stopwords])

def lemmatization(lemmatizer, text):
  return " ".join([lemmatizer.lemmatize(w) for w in text.split()])

train.comment_text = train.comment_text.apply(lower_case_normalization)
train.comment_text = train.comment_text.apply(clean_punct)
train.comment_text = train.comment_text.apply(lambda x : remove_stop_words(stops, x))
train.comment_text = train.comment_text.apply(lambda x : lemmatization(lmtzr, x))
train.comment_text.values[:5]


array(['explanation edits made username hardcore metallica fan closure gas voted new york doll please remove template talk page since retired',
       'match background colour seemingly stuck january',
       'hey really trying edit guy constantly removing relevant information talking edits instead talk seems care formatting actual',
       'make real suggestion improvement wondered section statistic later subsection think reference may need tidying exact format ie date format later else first preference formatting style reference want please let appears backlog article review guess may delay reviewer turn listed relevant form eg',
       'chance remember page'], dtype=object)

# **Visualization**


In [ ]:
train.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  explanation edits made username hardcore metal...      0   
1  000103f0d9cfb60f    match background colour seemingly stuck january      0   
2  000113f07ec002fd  hey really trying edit guy constantly removing...      0   
3  0001b41b1c6bb37e  make real suggestion improvement wondered sect...      0   
4  0001d958c54c6e35                               chance remember page      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [ ]:
# Comment Length Distributions By Number of Words
def comment_len_hist():
  comment_len = np.array([len(txt) for txt in train.loc[:, "comment_text"]])
  fig = px.histogram(comment_len, marginal="box")
  fig.update_layout(
    title = "Comment Length Distributions By Number of Words",
    xaxis_title = "Number of Words",
    yaxis_title = "Frequency",  
  )
  fig.show()
comment_len_hist()

In [ ]:
# Word Cloud of Comments
def word_cloud(data):
  wordcloud = WordCloud(
    background_color = "white",
    stopwords = stops,
    max_words = 300,
    max_font_size = 50,
    scale = 3,
    random_state = True
  )

  wordcloud = wordcloud.generate(str(data))

  fig = plt.figure(1, figsize = (12, 12))
  plt.axis('off')
  plt.imshow(wordcloud)
  plt.show()

word_cloud(train.loc[:, 'comment_text'])

In [ ]:
# Sentiment Analysis
def polarity(data):
  return TextBlob(data).sentiment.polarity

def sentiment_analysis():
  polarities = [polarity(text) for text in train.loc[:, 'comment_text']]
  fig = px.histogram(polarities, marginal = "box")
  fig.update_layout(
    title = "Sentiment Distributions of Comments",
    xaxis_title = "Sentiment Score",
    yaxis_title = "Frequency"    
  )

  fig.show()
sentiment_analysis()

In [ ]:
# Name Entity Resolution
def show_ner():
  ner_result = nlp_ner_model(train.loc[0, "comment_text"])
  print(train.loc[0, "comment_text"])
  spacy.displacy.render(ner_result, style='ent', jupyter=True)
show_ner()

explanation edits made username hardcore metallica fan closure gas voted new york doll please remove template talk page since retired


#**Feature Engineering**

## Examples

1-gram

In [ ]:
def one_gram_feature_extract_eg():
  #corpus = train.loc[:, 'comment_text'].tolist()
  corpus = [
    'I have been heaven’s substitute to recompense the good',
    'the god of vengeance yields to me his power to punish the wicked!',
  ]
  vectorizer = CountVectorizer()
  features = vectorizer.fit_transform(corpus)
  analyze = vectorizer.build_analyzer()
  print(vectorizer.get_feature_names_out())
  print(features.toarray())
  print(analyze('the god of vengeance yields to me his power to punish the wicked!'))
  print(vectorizer.transform(['the yacht headed out to the sea']).toarray())   

one_gram_feature_extract_eg()

['been' 'god' 'good' 'have' 'heaven' 'his' 'me' 'of' 'power' 'punish'
 'recompense' 'substitute' 'the' 'to' 'vengeance' 'wicked' 'yields']
[[1 0 1 1 1 0 0 0 0 0 1 1 1 1 0 0 0]
 [0 1 0 0 0 1 1 1 1 1 0 0 2 2 1 1 1]]
['the', 'god', 'of', 'vengeance', 'yields', 'to', 'me', 'his', 'power', 'to', 'punish', 'the', 'wicked']
[[0 0 0 0 0 0 0 0 0 0 0 0 2 1 0 0 0]]


n-gram

In [ ]:
def n_gram_feature_extract(num):
  #corpus = train.loc[:, 'comment_text'].tolist()
  corpus = [
    'I have been heaven’s substitute to recompense the good',
    'the god of vengeance yields to me his power to punish the wicked!',
  ]
  vectorizer = CountVectorizer(ngram_range=(1,2))
  features = vectorizer.fit_transform(corpus)
  analyze = vectorizer.build_analyzer()
  print(vectorizer.get_feature_names_out())
  print(features.toarray())
  print(analyze('the god of vengeance yields to me his power to punish the wicked!'))
  print(vectorizer.transform(['the yacht headed out to the sea']).toarray())   

n_gram_feature_extract_eg(2)

['been' 'been heaven' 'god' 'god of' 'good' 'have' 'have been' 'heaven'
 'heaven substitute' 'his' 'his power' 'me' 'me his' 'of' 'of vengeance'
 'power' 'power to' 'punish' 'punish the' 'recompense' 'recompense the'
 'substitute' 'substitute to' 'the' 'the god' 'the good' 'the wicked' 'to'
 'to me' 'to punish' 'to recompense' 'vengeance' 'vengeance yields'
 'wicked' 'yields' 'yields to']
[[1 1 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 1 0 1 0 0 1 0 0 0 0 0]
 [0 0 1 1 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 0 0 0 0 2 1 0 1 2 1 1 0 1 1 1 1 1]]
['the', 'god', 'of', 'vengeance', 'yields', 'to', 'me', 'his', 'power', 'to', 'punish', 'the', 'wicked', 'the god', 'god of', 'of vengeance', 'vengeance yields', 'yields to', 'to me', 'me his', 'his power', 'power to', 'to punish', 'punish the', 'the wicked']
[[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2 0 0 0 1 0 0 0 0 0 0 0 0]]


TF-IDF

In [16]:
def tf_idf():
  #corpus = train.loc[:, 'comment_text'].tolist()
  corpus = [
    'I have been heaven’s substitute to recompense the good',
    'the god of vengeance yields to me his power to punish the wicked!',
  ]
  count_vector = CountVectorizer()
  freq = count_vector.fit_transform(corpus)
  
  transformer = TfidfTransformer(smooth_idf=False)
  tfidf = transformer.fit_transform(freq)  
  print(tfidf.toarray())

tf_idf_eg()

[[0.38640134 0.         0.38640134 0.38640134 0.38640134 0.
  0.         0.         0.         0.         0.38640134 0.38640134
  0.22821485 0.22821485 0.         0.         0.        ]
 [0.         0.29122704 0.         0.         0.         0.29122704
  0.29122704 0.29122704 0.29122704 0.29122704 0.         0.
  0.34400676 0.34400676 0.29122704 0.29122704 0.29122704]]


# Classification